In [1]:
### lrasmy@Zhilab last revised August 1 2021   ##
###############################################

## Extract The in-hospital Mortality Data

### Import the required packages


In [1]:
import numpy as np
import pandas as pd
import sys
import importlib
from mimic4_preprocess_util import *

mimic4_path='mimiciv/1.0/'
verbose= True
output_path='extracted_data'
if not os.path.exists(output_path):
        os.makedirs(output_path)

In [6]:
importlib.reload(mimic4_preprocess_util.py)

NameError: name 'mimic4_preprocess_util' is not defined

In [7]:
from mimic4_preprocess_util import *

In [8]:
stays = read_icustays_table(mimic4_path)
stays=stays.reset_index()
stays.head()

subject_id   hadm_id   stay_id       first_careunit        last_careunit  \
0    17867402  24528534  31793211  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
1    14435996  28960964  31983544  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
2    17609946  27385897  33183475  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
3    18966770  23483021  34131444  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
4    12776735  20817525  34547665       Neuro Stepdown       Neuro Stepdown   

               intime             outtime       los  
0 2154-03-03 04:11:00 2154-03-04 18:16:56  1.587454  
1 2150-06-19 17:57:00 2150-06-22 18:33:54  3.025625  
2 2138-02-05 18:54:00 2138-02-15 12:42:05  9.741725  
3 2123-10-25 10:35:00 2123-10-25 18:59:47  0.350544  
4 2200-07-12 00:33:00 2200-07-13 16:44:40  1.674769

In [9]:
if verbose:
    print('START:', stays.stay_id.unique().shape[0], stays.hadm_id.unique().shape[0],
          stays.subject_id.unique().shape[0])
print(min(stays['subject_id']),max(stays['subject_id']))

START: 76540 69211 53150
10000032 19999987


In [10]:
stays.shape

(76540, 8)

In [11]:
admits = read_admissions_table(mimic4_path)
admits.head()

subject_id   hadm_id           admittime           dischtime deathtime  \
0    14679932  21038362 2139-09-26 14:16:00 2139-09-28 11:30:00       NaT   
1    15585972  24941086 2123-10-07 23:56:00 2123-10-12 11:22:00       NaT   
2    11989120  21965160 2147-01-14 09:00:00 2147-01-17 14:25:00       NaT   
3    17817079  24709883 2165-12-27 17:33:00 2165-12-31 21:18:00       NaT   
4    15078341  23272159 2122-08-28 08:48:00 2122-08-30 12:32:00       NaT   

                ethnicity  
0                 UNKNOWN  
1                   WHITE  
2                 UNKNOWN  
3                   OTHER  
4  BLACK/AFRICAN AMERICAN

In [12]:
stays = merge_on_subject_admission(stays, admits)
print(min(stays['subject_id']),max(stays['subject_id']))
stays.head()

10000032 19999987


subject_id   hadm_id   stay_id       first_careunit        last_careunit  \
0    17867402  24528534  31793211  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
1    14435996  28960964  31983544  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
2    17609946  27385897  33183475  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
3    18966770  23483021  34131444  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
4    12776735  20817525  34547665       Neuro Stepdown       Neuro Stepdown   

               intime             outtime       los           admittime  \
0 2154-03-03 04:11:00 2154-03-04 18:16:56  1.587454 2154-03-03 03:09:00   
1 2150-06-19 17:57:00 2150-06-22 18:33:54  3.025625 2150-06-19 13:07:00   
2 2138-02-05 18:54:00 2138-02-15 12:42:05  9.741725 2138-02-05 17:42:00   
3 2123-10-25 10:35:00 2123-10-25 18:59:47  0.350544 2123-10-25 09:37:00   
4 2200-07-12 00:33:00 2200-07-13 16:44:40  1.674769 2200-07-11 22:46:00   

            dischtime           deathtime         ethnicity  
0 2154-03-04 16:30:00                 NaT  UNABLE TO OBTAIN  
1 2150-06-25 15:36:00                 NaT             WHITE  
2 2138-02-15 11:00:00 2138-02-15 11:00:00             WHITE  
3 2123-10-26 11:00:00                 NaT             WHITE  
4 2200-07-19 12:00:00                 NaT             OTHER

In [13]:
stays.shape

(76540, 12)

In [14]:
pt=pd.read_csv('mimiciv/1.0/core/patients.csv.gz', compression='gzip', header=0, index_col=0)
pt.head()

gender  anchor_age  anchor_year anchor_year_group  dod
subject_id                                                       
10000048        F          23         2126       2008 - 2010  NaN
10002723        F           0         2128       2017 - 2019  NaN
10003939        M           0         2184       2008 - 2010  NaN
10004222        M           0         2161       2014 - 2016  NaN
10005325        F           0         2154       2011 - 2013  NaN

In [15]:
patients = read_patients_table(mimic4_path)
print(patients.shape,patients.subject_id.unique().shape[0])
patients.head()

(382278, 6) 382278


subject_id gender dod  anchor_age  anchor_year   yob
0    10000048      F NaT          23         2126  2103
1    10002723      F NaT           0         2128  2128
2    10003939      M NaT           0         2184  2184
3    10004222      M NaT           0         2161  2161
4    10005325      F NaT           0         2154  2154

In [16]:
stays = merge_on_subject(stays, patients)
print(stays.shape)
stays.head()

(76540, 17)


subject_id   hadm_id   stay_id       first_careunit        last_careunit  \
0    17867402  24528534  31793211  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
1    14435996  28960964  31983544  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
2    17609946  27385897  33183475  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
3    18966770  23483021  34131444  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
4    12776735  20817525  34547665       Neuro Stepdown       Neuro Stepdown   

               intime             outtime       los           admittime  \
0 2154-03-03 04:11:00 2154-03-04 18:16:56  1.587454 2154-03-03 03:09:00   
1 2150-06-19 17:57:00 2150-06-22 18:33:54  3.025625 2150-06-19 13:07:00   
2 2138-02-05 18:54:00 2138-02-15 12:42:05  9.741725 2138-02-05 17:42:00   
3 2123-10-25 10:35:00 2123-10-25 18:59:47  0.350544 2123-10-25 09:37:00   
4 2200-07-12 00:33:00 2200-07-13 16:44:40  1.674769 2200-07-11 22:46:00   

            dischtime           deathtime         ethnicity gender        dod  \
0 2154-03-04 16:30:00                 NaT  UNABLE TO OBTAIN      M        NaT   
1 2150-06-25 15:36:00                 NaT             WHITE      M        NaT   
2 2138-02-15 11:00:00 2138-02-15 11:00:00             WHITE      M 2138-02-15   
3 2123-10-26 11:00:00                 NaT             WHITE      M        NaT   
4 2200-07-19 12:00:00                 NaT             OTHER      M        NaT   

   anchor_age  anchor_year   yob  
0          25         2154  2129  
1          42         2143  2101  
2          70         2138  2068  
3          87         2123  2036  
4          72         2192  2120

In [17]:
print('latest stay cnts:', stays.stay_id.unique().shape[0], stays.hadm_id.unique().shape[0],
         stays.subject_id.unique().shape[0])

latest stay cnts: 76540 69211 53150


In [18]:
stays = add_age_to_icustays(stays)
stays = add_inunit_mortality_to_icustays(stays)
print(stays.shape)
stays.head()

(76540, 19)


subject_id   hadm_id   stay_id       first_careunit        last_careunit  \
0    17867402  24528534  31793211  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
1    14435996  28960964  31983544  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
2    17609946  27385897  33183475  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
3    18966770  23483021  34131444  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
4    12776735  20817525  34547665       Neuro Stepdown       Neuro Stepdown   

               intime             outtime       los           admittime  \
0 2154-03-03 04:11:00 2154-03-04 18:16:56  1.587454 2154-03-03 03:09:00   
1 2150-06-19 17:57:00 2150-06-22 18:33:54  3.025625 2150-06-19 13:07:00   
2 2138-02-05 18:54:00 2138-02-15 12:42:05  9.741725 2138-02-05 17:42:00   
3 2123-10-25 10:35:00 2123-10-25 18:59:47  0.350544 2123-10-25 09:37:00   
4 2200-07-12 00:33:00 2200-07-13 16:44:40  1.674769 2200-07-11 22:46:00   

            dischtime           deathtime         ethnicity gender        dod  \
0 2154-03-04 16:30:00                 NaT  UNABLE TO OBTAIN      M        NaT   
1 2150-06-25 15:36:00                 NaT             WHITE      M        NaT   
2 2138-02-15 11:00:00 2138-02-15 11:00:00             WHITE      M 2138-02-15   
3 2123-10-26 11:00:00                 NaT             WHITE      M        NaT   
4 2200-07-19 12:00:00                 NaT             OTHER      M        NaT   

   anchor_age  anchor_year   yob  age  mortality_inunit  
0          25         2154  2129   25                 0  
1          42         2143  2101   49                 0  
2          70         2138  2068   70                 1  
3          87         2123  2036   87                 0  
4          72         2192  2120   80                 0

In [19]:
stays = add_inhospital_mortality_to_icustays(stays)
print(stays.shape)
stays.head()

(76540, 21)


subject_id   hadm_id   stay_id       first_careunit        last_careunit  \
0    17867402  24528534  31793211  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
1    14435996  28960964  31983544  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
2    17609946  27385897  33183475  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
3    18966770  23483021  34131444  Trauma SICU (TSICU)  Trauma SICU (TSICU)   
4    12776735  20817525  34547665       Neuro Stepdown       Neuro Stepdown   

               intime             outtime       los           admittime  \
0 2154-03-03 04:11:00 2154-03-04 18:16:56  1.587454 2154-03-03 03:09:00   
1 2150-06-19 17:57:00 2150-06-22 18:33:54  3.025625 2150-06-19 13:07:00   
2 2138-02-05 18:54:00 2138-02-15 12:42:05  9.741725 2138-02-05 17:42:00   
3 2123-10-25 10:35:00 2123-10-25 18:59:47  0.350544 2123-10-25 09:37:00   
4 2200-07-12 00:33:00 2200-07-13 16:44:40  1.674769 2200-07-11 22:46:00   

            dischtime  ...         ethnicity gender        dod anchor_age  \
0 2154-03-04 16:30:00  ...  UNABLE TO OBTAIN      M        NaT         25   
1 2150-06-25 15:36:00  ...             WHITE      M        NaT         42   
2 2138-02-15 11:00:00  ...             WHITE      M 2138-02-15         70   
3 2123-10-26 11:00:00  ...             WHITE      M        NaT         87   
4 2200-07-19 12:00:00  ...             OTHER      M        NaT         72   

   anchor_year   yob  age  mortality_inunit  mortality  mortality_inhospital  
0         2154  2129   25                 0          0                     0  
1         2143  2101   49                 0          0                     0  
2         2138  2068   70                 1          1                     1  
3         2123  2036   87                 0          0                     0  
4         2192  2120   80                 0          0                     0  

[5 rows x 21 columns]

In [20]:
### Quality check
#stays[(stays['mortality']==1) & (stays['deathtime'].isna()) ]

In [21]:
diagnosis = pd.read_csv(mimic4_path+'/hosp/diagnoses_icd.csv.gz', compression='gzip', header=0)
admis = pd.read_csv(mimic4_path+'/core/admissions.csv.gz', compression='gzip', header=0)
proc= pd.read_csv(mimic4_path+'/hosp/procedures_icd.csv.gz', compression='gzip', header=0)

In [22]:
diagnosis.head()

subject_id   hadm_id  seq_num icd_code  icd_version
0    15734973  20475282        3     2825            9
1    15734973  20475282        2    V0251            9
2    15734973  20475282        5     V270            9
3    15734973  20475282        1    64891            9
4    15734973  20475282        4    66481            9

In [23]:
admis.head()

subject_id   hadm_id            admittime            dischtime deathtime  \
0    14679932  21038362  2139-09-26 14:16:00  2139-09-28 11:30:00       NaN   
1    15585972  24941086  2123-10-07 23:56:00  2123-10-12 11:22:00       NaN   
2    11989120  21965160  2147-01-14 09:00:00  2147-01-17 14:25:00       NaN   
3    17817079  24709883  2165-12-27 17:33:00  2165-12-31 21:18:00       NaN   
4    15078341  23272159  2122-08-28 08:48:00  2122-08-30 12:32:00       NaN   

  admission_type admission_location discharge_location insurance language  \
0       ELECTIVE                NaN               HOME     Other  ENGLISH   
1       ELECTIVE                NaN               HOME     Other  ENGLISH   
2       ELECTIVE                NaN               HOME     Other  ENGLISH   
3       ELECTIVE                NaN               HOME     Other  ENGLISH   
4       ELECTIVE                NaN               HOME     Other  ENGLISH   

  marital_status               ethnicity edregtime edouttime  \
0         SINGLE                 UNKNOWN       NaN       NaN   
1            NaN                   WHITE       NaN       NaN   
2            NaN                 UNKNOWN       NaN       NaN   
3            NaN                   OTHER       NaN       NaN   
4            NaN  BLACK/AFRICAN AMERICAN       NaN       NaN   

   hospital_expire_flag  
0                     0  
1                     0  
2                     0  
3                     0  
4                     0

In [24]:
proc.head()

subject_id   hadm_id  seq_num   chartdate icd_code  icd_version
0    10287061  27485182        1  2124-08-22     7569            9
1    13135573  22286210        3  2187-05-30     7309            9
2    13135573  22286210        1  2187-05-30     7569            9
3    13135573  22286210        2  2187-05-30      734            9
4    12646116  24154012        2  2115-01-13      734            9

In [25]:
diagnosis.icd_code.unique().shape[0]

27170

In [26]:
proc.icd_code.unique().shape[0]

13016

In [27]:
### Cases for patient level prediction using the last ICU stay
case_pts= stays[['subject_id','intime','dischtime','deathtime']][stays['mortality']== 1]
case_pts['deathtime']=case_pts['deathtime'].fillna(case_pts['dischtime'])
case_pts_index= case_pts.groupby('subject_id')[['intime','deathtime']].max().reset_index()
case_pts_index['tte']=(pd.to_datetime(case_pts_index['deathtime'])-pd.to_datetime(case_pts_index['intime'])).dt.days
case_adm=admis[admis['subject_id'].isin(case_pts['subject_id'].drop_duplicates().tolist())] 

In [28]:
case_adm['subject_id'].nunique()

7304

In [29]:
case_adm.head()

subject_id   hadm_id            admittime            dischtime  \
7047    11407769  22195798  2188-06-27 10:31:00  2188-06-28 23:37:00   
7679    12932363  23434067  2123-07-09 23:04:00  2123-07-10 12:30:00   
7720    19231238  29766591  2183-03-16 18:46:00  2183-03-17 21:02:00   
7796    15461582  29778956  2181-08-10 00:00:00  2181-08-11 12:32:00   
7806    11540785  24330323  2134-03-24 18:20:00  2134-03-26 13:45:00   

     deathtime      admission_type      admission_location discharge_location  \
7047       NaN            EW EMER.                    PACU                NaN   
7679       NaN      EU OBSERVATION          EMERGENCY ROOM                NaN   
7720       NaN      EU OBSERVATION          EMERGENCY ROOM                NaN   
7796       NaN  DIRECT OBSERVATION  TRANSFER FROM HOSPITAL                NaN   
7806       NaN      EU OBSERVATION          EMERGENCY ROOM                NaN   

     insurance language marital_status               ethnicity  \
7047     Other  ENGLISH            NaN                 UNKNOWN   
7679     Other  ENGLISH         SINGLE                   WHITE   
7720  Medicare  ENGLISH        WIDOWED  BLACK/AFRICAN AMERICAN   
7796  Medicare  ENGLISH        MARRIED         HISPANIC/LATINO   
7806  Medicaid  ENGLISH        WIDOWED                   WHITE   

                edregtime            edouttime  hospital_expire_flag  
7047                  NaN                  NaN                     0  
7679  2123-07-09 22:51:00  2123-07-09 22:51:00                     0  
7720  2183-03-15 21:06:00  2183-03-16 20:08:00                     0  
7796                  NaN                  NaN                     0  
7806  2134-03-24 11:28:00  2134-03-24 19:17:00                     0

In [30]:
case_pts_index.head()

subject_id              intime           deathtime  tte
0    10001884 2131-01-11 04:20:05 2131-01-20 05:15:00    9
1    10002155 2131-03-09 21:33:00 2131-03-10 21:53:00    1
2    10003400 2137-08-17 17:36:37 2137-09-02 17:05:00   15
3    10004401 2144-06-05 20:36:00 2144-06-18 21:30:00   13
4    10004720 2186-11-12 19:55:00 2186-11-17 18:30:00    4

In [31]:
case_pts_index.shape

(7304, 4)

In [32]:
case_adm1=pd.merge(case_pts_index,case_adm, right_on='subject_id', left_on='subject_id') 
case_adm2=case_adm1[pd.to_datetime(case_adm1['admittime']) <= case_adm1['intime']] #25,427 records

In [33]:
case_adm2.shape

(25427, 18)

In [34]:
case_adm2['subject_id'].nunique()

7303

In [35]:
case_adm2.head()

subject_id              intime         deathtime_x  tte   hadm_id  \
0    10001884 2131-01-11 04:20:05 2131-01-20 05:15:00    9  27016754   
1    10001884 2131-01-11 04:20:05 2131-01-20 05:15:00    9  29675586   
2    10001884 2131-01-11 04:20:05 2131-01-20 05:15:00    9  21192799   
3    10001884 2131-01-11 04:20:05 2131-01-20 05:15:00    9  27765344   
4    10001884 2131-01-11 04:20:05 2131-01-20 05:15:00    9  21577720   

             admittime            dischtime deathtime_y      admission_type  \
0  2130-06-23 22:14:00  2130-06-24 11:07:00         NaN      EU OBSERVATION   
1  2130-04-08 22:06:00  2130-04-09 14:30:00         NaN      EU OBSERVATION   
2  2130-10-05 20:04:00  2130-10-06 15:05:00         NaN      EU OBSERVATION   
3  2127-12-11 18:06:00  2127-12-12 13:46:00         NaN  DIRECT OBSERVATION   
4  2125-12-26 17:06:00  2125-12-27 16:52:00         NaN      EU OBSERVATION   

   admission_location discharge_location insurance language marital_status  \
0      EMERGENCY ROOM                NaN  Medicare  ENGLISH        MARRIED   
1      EMERGENCY ROOM                NaN  Medicare  ENGLISH        MARRIED   
2      EMERGENCY ROOM                NaN  Medicare  ENGLISH        MARRIED   
3  PHYSICIAN REFERRAL                NaN  Medicare  ENGLISH        MARRIED   
4      EMERGENCY ROOM                NaN  Medicare  ENGLISH        MARRIED   

                ethnicity            edregtime            edouttime  \
0  BLACK/AFRICAN AMERICAN  2130-06-23 17:42:00  2130-06-24 11:07:00   
1  BLACK/AFRICAN AMERICAN  2130-04-08 15:58:00  2130-04-08 22:46:00   
2  BLACK/AFRICAN AMERICAN  2130-10-05 11:58:00  2130-10-06 15:05:00   
3  BLACK/AFRICAN AMERICAN                  NaN                  NaN   
4  BLACK/AFRICAN AMERICAN  2125-12-26 13:50:00  2125-12-26 18:17:00   

   hospital_expire_flag  
0                     0  
1                     0  
2                     0  
3                     0  
4                     0

##### Quick Quality check

In [66]:
#case_adm2[case_adm2['admittime']>case_adm2['dischtime']] ### good
case_adm2[case_adm2['admittime']>case_adm2['deathtime_y']] ### good

Empty DataFrame
Columns: [subject_id, intime, deathtime_x, tte, hadm_id, admittime, dischtime, deathtime_y, admission_type, admission_location, discharge_location, insurance, language, marital_status, ethnicity, edregtime, edouttime, hospital_expire_flag]
Index: []

In [36]:
### Extract diagnosis data for cases
case_diag=diagnosis[(diagnosis['subject_id'].isin(case_adm2['subject_id'].drop_duplicates().tolist()))&(diagnosis['hadm_id'].isin(case_adm2['hadm_id'].drop_duplicates().tolist()))]
case_diag=case_diag.merge(case_adm2[['subject_id','hadm_id','admittime','dischtime']].drop_duplicates(),how='left')
case_diag.head()

subject_id   hadm_id  seq_num icd_code  icd_version            admittime  \
0    16415791  25735682        5    V1005            9  2162-11-17 00:04:00   
1    16415791  25735682        2     6826            9  2162-11-17 00:04:00   
2    16415791  25735682        3     5990            9  2162-11-17 00:04:00   
3    16415791  25735682        4     4019            9  2162-11-17 00:04:00   
4    16415791  25735682        6     7821            9  2162-11-17 00:04:00   

             dischtime  
0  2163-04-03 10:44:00  
1  2163-04-03 10:44:00  
2  2163-04-03 10:44:00  
3  2163-04-03 10:44:00  
4  2163-04-03 10:44:00

In [37]:
case_diag['dischtime']=pd.to_datetime(case_diag['dischtime']).dt.date
case_diag['event_code']='D_ICD'+case_diag['icd_version'].astype('str')+'_'+case_diag['icd_code']
case_diag=case_diag[['subject_id','event_code','dischtime']].drop_duplicates()
case_diag.head()

subject_id    event_code   dischtime
0    16415791  D_ICD9_V1005  2163-04-03
1    16415791   D_ICD9_6826  2163-04-03
2    16415791   D_ICD9_5990  2163-04-03
3    16415791   D_ICD9_4019  2163-04-03
4    16415791   D_ICD9_7821  2163-04-03

In [38]:
### Extract procedure data for cases
case_proc=proc[(proc['subject_id'].isin(case_adm2['subject_id'].drop_duplicates().tolist()))&(proc['hadm_id'].isin(case_adm2['hadm_id'].drop_duplicates().tolist()))]
case_proc=case_proc.merge(case_pts_index.drop_duplicates(),how='left')
case_proc.head()

subject_id   hadm_id  seq_num   chartdate icd_code  icd_version  \
0    12646269  21934639        1  2176-12-08      596            9   
1    12646269  21934639        4  2176-12-08     7095            9   
2    12646269  21934639        2  2176-12-08     7050            9   
3    12646269  21934639        3  2176-12-08     7078            9   
4    12844772  26061183        1  2199-06-02     9671            9   

               intime           deathtime  tte  
0 2181-09-22 08:37:00 2181-09-24 00:21:00    1  
1 2181-09-22 08:37:00 2181-09-24 00:21:00    1  
2 2181-09-22 08:37:00 2181-09-24 00:21:00    1  
3 2181-09-22 08:37:00 2181-09-24 00:21:00    1  
4 2211-01-14 14:37:00 2211-01-17 12:34:00    2

In [68]:
case_proc=case_proc[pd.to_datetime(case_proc['chartdate']) <= case_proc['intime']] ### only to keep events occur before the index date
case_proc=case_proc.merge(case_adm2[['subject_id','hadm_id','admittime','dischtime']].drop_duplicates(),how='left')
case_proc['dischtime']=pd.to_datetime(case_proc['dischtime']).dt.date
case_proc['event_code']='P_ICD'+ case_proc['icd_version'].astype('str')+'_'+case_proc['icd_code']
case_proc=case_proc[['subject_id','event_code','dischtime']].drop_duplicates()

In [69]:
### ctrls for patient level prediction using the last ICU stay

ctrl_pts= stays[['subject_id','intime','dischtime']][~(stays['subject_id'].isin(case_pts['subject_id'].drop_duplicates().tolist()))]
ctrl_pts.columns=['subject_id','intime','last_dischtime']
ctrl_pts_index= ctrl_pts.groupby('subject_id')[['intime','last_dischtime']].max().reset_index()
ctrl_pts_index['tte']=(pd.to_datetime(ctrl_pts_index['last_dischtime'])-pd.to_datetime(ctrl_pts_index['intime'])).dt.days
ctrl_adm=admis[admis['subject_id'].isin(ctrl_pts['subject_id'].drop_duplicates().tolist())] 
ctrl_adm1=pd.merge(ctrl_pts_index,ctrl_adm, right_on='subject_id', left_on='subject_id') 
ctrl_adm2=ctrl_adm1[pd.to_datetime(ctrl_adm1['admittime']) <= ctrl_adm1['intime']] 

In [70]:
### Extract diagnosis data for ctrl

ctrl_diag=diagnosis[(diagnosis['subject_id'].isin(ctrl_adm2['subject_id'].drop_duplicates().tolist()))&(diagnosis['hadm_id'].isin(ctrl_adm2['hadm_id'].drop_duplicates().tolist()))]
ctrl_diag=ctrl_diag.merge(ctrl_adm2[['subject_id','hadm_id','admittime','dischtime']].drop_duplicates(),how='left')
ctrl_diag['dischtime']=pd.to_datetime(ctrl_diag['dischtime']).dt.date
ctrl_diag['event_code']='D_ICD'+ctrl_diag['icd_version'].astype('str')+'_'+ctrl_diag['icd_code']
ctrl_diag=ctrl_diag[['subject_id','event_code','dischtime']].drop_duplicates()

In [71]:
### Extract procedure data for ctrl
ctrl_proc=proc[(proc['subject_id'].isin(ctrl_adm2['subject_id'].drop_duplicates().tolist()))&(proc['hadm_id'].isin(ctrl_adm2['hadm_id'].drop_duplicates().tolist()))]
ctrl_proc=ctrl_proc.merge(ctrl_pts_index.drop_duplicates(),how='left')
ctrl_proc=ctrl_proc[pd.to_datetime(ctrl_proc['chartdate']) <= ctrl_proc['intime']] ### only to keep events occur before the index date
ctrl_proc=ctrl_proc.merge(ctrl_adm2[['subject_id','hadm_id','admittime','dischtime']].drop_duplicates(),how='left')
ctrl_proc['dischtime']=pd.to_datetime(ctrl_proc['dischtime']).dt.date
ctrl_proc['event_code']='P_ICD'+ ctrl_proc['icd_version'].astype('str')+'_'+ctrl_proc['icd_code']
ctrl_proc=ctrl_proc[['subject_id','event_code','dischtime']].drop_duplicates()

In [72]:
case_diag.head()

subject_id    event_code   dischtime
0    16415791  D_ICD9_V1005  2163-04-03
1    16415791   D_ICD9_6826  2163-04-03
2    16415791   D_ICD9_5990  2163-04-03
3    16415791   D_ICD9_4019  2163-04-03
4    16415791   D_ICD9_7821  2163-04-03

In [73]:
case_proc.head()

subject_id   event_code   dischtime
0    12646269   P_ICD9_596  2176-12-10
1    12646269  P_ICD9_7095  2176-12-10
2    12646269  P_ICD9_7050  2176-12-10
3    12646269  P_ICD9_7078  2176-12-10
4    12844772  P_ICD9_9671  2199-06-09

In [74]:
ctrl_diag.head()

subject_id    event_code   dischtime
0    11560010  D_ICD9_64413  2163-06-04
1    18115699   D_ICD9_3540  2164-05-16
2    18115699    D_ICD9_496  2164-05-16
3    18115699  D_ICD9_53081  2164-05-16
4    18115699   D_ICD9_5680  2164-05-16

In [75]:
ctrl_proc.head()

subject_id   event_code   dischtime
0    17101524  P_ICD9_4495  2184-02-25
1    19704964  P_ICD9_7359  2140-03-15
2    19704964  P_ICD9_6902  2140-03-15
3    19704964  P_ICD9_9904  2140-03-15
4    19704964   P_ICD9_754  2140-03-15

In [76]:
ctrl_pts_index.head()

subject_id              intime      last_dischtime  tte
0    10000032 2180-07-23 14:00:00 2180-07-25 17:55:00    2
1    10000980 2189-06-27 08:42:00 2189-07-03 03:00:00    5
2    10001217 2157-12-19 15:42:24 2157-12-24 14:55:00    4
3    10001725 2110-04-11 15:52:22 2110-04-14 15:00:00    2
4    10002013 2160-05-18 10:00:53 2160-05-23 13:30:00    5

In [77]:
case_pts_index.head()

subject_id              intime           deathtime  tte
0    10001884 2131-01-11 04:20:05 2131-01-20 05:15:00    9
1    10002155 2131-03-09 21:33:00 2131-03-10 21:53:00    1
2    10003400 2137-08-17 17:36:37 2137-09-02 17:05:00   15
3    10004401 2144-06-05 20:36:00 2144-06-18 21:30:00   13
4    10004720 2186-11-12 19:55:00 2186-11-17 18:30:00    4

In [78]:
### dump extracted data
pd.concat([case_diag,
           case_proc,
           ctrl_diag,
           ctrl_proc]
          ).dropna().to_csv(output_path+'/Mimic_PT_mortality_data_dp.tsv', sep='\t',index=False)

### dump labels, mortality label and time to death for survival

ctrl_pts_index['mort']=0
case_pts_index['mort']=1

pd.concat([ctrl_pts_index[['subject_id','mort','tte']].drop_duplicates(),
           case_pts_index[['subject_id','mort','tte']].drop_duplicates()
           ]).dropna().to_csv(output_path+'/Mimic_PT_mortality_labels.tsv', sep='\t',index=False)

## Proprocess data into pickled list



In [2]:
#sys.path.insert(0,"/content/drive/MyDrive/pytorch_ehr/Pytorch_EHR_Tutorial/Data_Prep/")
from preprocess_outcomes  import dump_split_process_data

In [3]:
output_proc='processed_data'
if not os.path.exists(output_proc):
        os.makedirs(output_proc)

dump_split_process_data(output_path+'/Mimic_PT_mortality_data_dp.tsv', output_path+'/Mimic_PT_mortality_labels.tsv' , 'NA' ,output_proc+'/Mimic_PT_mortality_dp_v1' , 'NA' )

loading data
loaded data for:  52926
loading labels
loaded labels for:  53150  after primary cleaning  52926
Mortality Case counts:  7303
LOS>7 :  15212
new types dictionary
processed 1000 pts
processed 2000 pts
processed 3000 pts
processed 4000 pts
processed 5000 pts
processed 6000 pts
processed 7000 pts
processed 8000 pts
processed 9000 pts
processed 10000 pts
processed 11000 pts
processed 12000 pts
processed 13000 pts
processed 14000 pts
processed 15000 pts
processed 16000 pts
processed 17000 pts
processed 18000 pts
processed 19000 pts
processed 20000 pts
processed 21000 pts
processed 22000 pts
processed 23000 pts
processed 24000 pts
processed 25000 pts
processed 26000 pts
processed 27000 pts
processed 28000 pts
processed 29000 pts
processed 30000 pts
processed 31000 pts
processed 32000 pts
processed 33000 pts
processed 34000 pts
processed 35000 pts
processed 36000 pts
processed 37000 pts
processed 38000 pts
processed 39000 pts
processed 40000 pts
processed 41000 pts
processed 42000

n_pt [10277287, [0, 1], [[[0], [1243, 1094, 357, 1580, 139, 360, 1189, 2174, 335, 323, 81, 86, 85, 1022, 351, 1587, 3981]]]]
n_pt [10277566, [0, 3], [[[0], [96, 1916, 5377, 1175, 372, 1910, 136, 139, 471, 86, 85, 4263, 790, 388, 114]]]]
n_pt [10277901, [1, 4], [[[0], [286, 36, 6, 26, 225, 159, 2036, 6261, 1215, 208, 25, 148, 30, 406, 219, 27, 738, 1, 38]], [[9], [1880, 26, 1720, 1970, 159, 38, 27, 312, 148, 1, 36, 185, 30, 25, 208, 935]], [[193], [300, 294, 53, 286, 6, 148, 293, 1618, 219, 153, 26, 738, 1256, 4318, 2474, 755, 312, 311, 5, 30, 601, 1346, 22, 758, 2036, 37, 25, 36, 147, 1754, 268, 608, 1]]]]
n_pt [10278142, [0, 1], [[[0], [175, 2059, 240, 10, 41, 60, 5205, 1769, 1999]]]]
n_pt [10278264, [0, 4], [[[0], [41, 301, 276, 6283, 6903, 6904, 6905]]]]
n_pt [10278344, [0, 5], [[[0], [2790, 87, 734, 2230, 2800, 6484, 6906, 4911, 329, 3455, 1378, 1179, 82, 2536, 909, 1401, 475, 81, 85, 122, 2278, 1086, 4376]]]]
n_pt [10279057, [0, 4], [[[0], [1612, 10, 153, 30, 559, 60, 32, 746, 381

n_pt [10514013, [0, 5], [[[0], [258, 266, 907, 81, 5479, 874, 877, 109, 2167]]]]
n_pt [10514375, [0, 5], [[[0], [891, 266, 1243, 2652, 113, 106, 117, 1517, 325, 3367, 1274]], [[247], [2076, 114, 266, 3298, 2388, 6789, 1266, 1243, 81, 334, 263, 2667, 325, 3376, 2789, 372, 705, 3367, 1701, 2450, 9186, 87]], [[732], [81, 3367, 2165, 266, 87, 1243, 334, 86, 9187, 325]], [[149], [331, 334, 113, 96, 260, 2667, 3028, 325, 3376, 881, 4252, 8074, 266, 9188, 3298, 705, 86, 1266, 87, 469, 1487, 81]], [[1268], [2038, 270, 532, 269, 5268, 32, 41, 760, 506]], [[26], [41, 5268, 445, 158, 447, 32, 269, 760, 1970, 270]], [[75], [32, 4098, 640, 4113, 167, 506, 5268, 213, 532, 2345, 269, 39, 71, 204, 760]], [[8], [5268, 239, 32, 1964, 228, 506, 269, 532, 547, 1120, 41, 760, 270]], [[551], [1173, 41, 270, 760, 284, 269, 1066, 3671]]]]
n_pt [10514512, [0, 3], [[[0], [2340, 270, 608, 506, 497, 5558, 532, 1605, 6, 9189]], [[310], [2340, 532, 236, 5592, 270, 497, 506, 6138, 973]]]]
n_pt [10514599, [0, 1], [[[

n_pt [10653932, [0, 7], [[[0], [167, 1005, 3860, 60, 1572, 5733, 3861, 298]], [[716], [1572, 742, 32, 658, 7095]]]]
n_pt [10654688, [1, 5], [[[0], [2036, 5268, 278, 3860, 5361, 595, 148, 219, 236, 934, 502, 20, 2949, 60, 6, 39, 49, 26, 569, 159, 182, 25, 51, 208, 3059]]]]
n_pt [10654750, [0, 7], [[[0], [595, 30, 381, 184, 188, 174, 187, 269, 194, 240, 276, 956, 27, 148, 236, 41, 157, 65, 32, 16, 2310]]]]
n_pt [10654923, [0, 8], [[[0], [1882, 1429, 1432, 3185, 1254, 120, 729, 1915, 81, 82, 1020, 86, 804, 1590, 136, 1031, 114, 1435, 722]]]]
n_pt [10655065, [0, 24], [[[0], [814, 367, 4763, 342, 10106, 10107, 88, 1112, 10108, 9764, 10109, 256, 78, 10110, 1243, 320, 10111, 802, 334, 466]]]]
n_pt [10655111, [0, 45], [[[0], [717, 623, 6645, 956, 27, 406, 644, 1304, 4841, 269, 234, 60, 8648, 8756, 276, 245, 10112, 10113, 278, 646, 219, 1832, 6738, 1651, 10114, 48, 525, 418, 5993, 65, 588, 10115, 656, 268, 10116, 10117, 934, 1846, 7211, 796, 980, 645]]]]
n_pt [10655269, [0, 4], [[[0], [81, 82, 

n_pt [10911585, [1, 5], [[[0], [11558, 1244, 691, 86, 1412, 107, 1127, 11559, 789, 263, 3204, 11560, 2487, 87, 1405, 1019, 9394, 5869, 1558, 82, 81, 10541, 351, 1278]]]]
n_pt [10911605, [0, 9], [[[0], [3117, 377, 236, 213, 2889, 308, 1586, 234, 283, 757, 1524, 502, 1306, 20, 839, 1877, 740, 990, 1314, 2885, 2887, 3151]], [[25], [3154, 2, 5, 25, 757, 502, 1586, 1847, 23, 287, 4, 990, 185, 284, 839]], [[58], [2510, 3234, 2356, 185, 14, 658, 757, 4282, 11, 238, 20, 19, 839, 2, 208]]]]
n_pt [10911778, [0, 67], [[[0], [358, 1950, 1690, 86, 2393, 784, 4955, 335, 5715, 2652, 1291, 85, 891, 342, 114, 1678, 138, 1029, 323, 1031, 331, 1396, 7966, 734]]]]
n_pt [10912090, [1, 4], [[[0], [7425, 342, 790, 11561, 75, 1245, 140, 1950, 11349, 825, 823, 104, 1157, 2393, 1679, 113, 791, 372, 1039, 1274, 1744, 1403, 115, 792, 3106, 1806, 734, 99, 3472, 1690, 691, 4215, 11562, 2458, 1154]], [[38], [1274, 372, 2535, 790, 792, 2458, 976, 3969]], [[78], [791, 1034, 96, 790, 792, 2458, 372, 822, 688, 117, 1048

...

n_pt [18958178, [0, 10], [[[0], [96, 1048, 722, 2535, 334, 3261, 266, 1805, 86, 468, 261, 136, 2869, 5063, 1741, 1127, 1594]]]]
n_pt [18958268, [0, 3], [[[0], [22, 156, 187, 230, 191, 161, 189, 190, 1, 5178, 34, 30, 39, 178, 10, 3255, 1222, 41, 188]]]]
n_pt [18958515, [1, 10], [[[0], [26474, 823, 734, 691, 1078, 790, 7631, 114, 6778, 1954, 8930, 2754, 3219, 1495, 1634, 4153, 105, 2789, 136, 104, 922, 3218, 471, 732, 26475, 99]]]]
n_pt [18958543, [0, 18], [[[0], [5271, 1243, 734, 725, 23012, 136, 114, 1497, 351, 138, 1272, 81, 10416, 477, 8004, 1086, 87, 266, 10315]]]]
n_pt [18958715, [0, 3], [[[0], [755, 502, 276, 425, 677, 855, 148, 33, 636, 856]]]]
n_pt [18958863, [0, 4], [[[0], [1179, 920, 14578, 98, 722, 721, 720, 719, 81, 1416, 130, 7022, 4276, 3659, 86, 353]], [[7], [130, 353, 7776, 920, 86, 1184, 1179, 81]]]]
n_pt [18958916, [0, 35], [[[0], [18375, 8884, 3796, 3543, 922, 96, 471, 114, 874, 909, 1200, 1950, 1130, 1804, 9391, 1744, 732, 475, 261, 1946, 877, 2157, 256, 1422, 492, 7

n_pt [19237156, [1, 0], [[[0], [53, 2944, 4001, 32, 41, 1167, 234, 1149, 306, 897, 39, 60, 2506, 542, 428, 12, 219, 1, 425, 755, 1304, 2053, 3955, 4891, 268, 1311, 295, 280, 639, 1330, 11033, 4972, 420, 10, 2581, 152, 408, 310, 185]], [[51], [425, 1330, 1524, 270, 521, 159, 41, 1149, 742, 24, 4001, 10, 32, 408, 152, 39, 1]], [[70], [425, 568, 26, 12, 1165, 1928, 64, 2506, 152, 181, 377, 2624, 65, 39, 41, 1874, 10, 1330, 10799, 31, 2721, 408, 60, 4970, 154]], [[59], [39, 568, 542, 3657, 5115, 742, 2721, 1, 425, 152, 428, 6999, 10, 897, 12, 9978, 41, 32]], [[60], [39, 2053, 425, 408, 1330, 441, 26, 22, 41, 181, 542, 10, 1, 2506, 897, 204, 1167, 428, 12, 270, 3036, 152, 2721, 651]], [[38], [12, 310, 311, 897, 289, 24, 542, 3742, 6565, 2053, 408, 420, 39, 32, 276, 441, 2721, 1, 651, 152, 185, 1167, 270, 549, 1606, 294, 6999, 306, 428, 1330, 19193, 22, 10799, 425, 10, 1583, 742, 41, 5115, 314]], [[97], [1, 1167, 270, 1324, 425, 6565, 12, 1316, 289, 2506, 6134, 24, 408, 428, 434, 39, 2721, 6

n_pt [19480385, [0, 11], [[[0], [65, 145, 280, 300, 1224, 219, 3363, 4295, 55, 1351, 278, 3955, 851, 10, 12144, 1457, 657, 8978]], [[263], [154, 1774, 41, 55]]]]
n_pt [19480392, [0, 4], [[[0], [561, 1167, 2775, 60, 1845, 56, 1610, 65, 10398, 2011, 52]]]]
n_pt [19480678, [0, 2], [[[0], [218, 1599, 172, 41, 269, 11, 270, 1757, 2033, 2036, 151, 11891, 1061]]]]
n_pt [19480985, [1, 2], [[[0], [317, 1296, 1570, 1399, 333, 330, 10250, 352, 1280, 481, 107, 96, 1178, 823, 5749, 1744, 346, 490, 104, 907, 2280, 1031, 1852, 1139, 100, 1138, 484, 734, 691, 15505, 1687, 99, 1135, 75, 1297, 905, 3078, 91, 874, 113, 791, 709]], [[551], [114, 4758, 1296, 1293, 330, 1399, 1517, 2649, 705, 387, 2207, 317, 2280, 1435, 477, 1297, 96, 86, 333, 2652, 907, 1243]], [[2044], [5357, 1330, 544, 22602, 41, 1222, 22, 450, 178, 1533, 39]], [[134], [2, 618, 450, 185, 2376, 1330, 41, 1754, 408]], [[586], [27, 41, 3156, 935, 949, 4073, 1362, 1828]], [[11], [3791, 41, 1532, 949, 1360, 2902, 1362, 4006, 1361, 408, 1871]]

n_pt [19707067, [0, 5], [[[0], [2960, 319, 333, 81, 255, 114, 86, 90, 1088, 96, 334, 1428, 1179, 85, 131, 556, 2958]], [[3846], [11, 381, 670, 1301, 3933, 184, 301, 32, 625, 21, 39, 3450, 1893, 31, 65, 34, 183, 6258, 41, 195, 156, 186, 30, 148, 450]], [[107], [162, 301, 746, 41, 1777, 30, 161, 232, 187, 190, 188, 1016, 33, 32, 2271, 1612, 3450]]]]
n_pt [19707325, [1, 1], [[[0], [790, 114, 4483, 116, 1175, 334, 79, 319, 824, 316, 330, 77, 823, 3096, 1019, 6598, 113, 492, 86, 125, 326, 3516, 107, 96, 361, 465, 342, 804, 1045, 1656, 85]]]]
n_pt [19707700, [0, 9], [[[0], [143, 791, 79, 1035, 907, 81, 116, 1519, 1125, 353, 492, 335, 1254, 5394, 874, 334, 823, 132, 107, 734, 372, 1201, 1205, 475, 13890, 85, 3707]], [[26], [4557, 8492, 7708, 5892, 6121, 5314, 7832, 20618, 25822, 7356, 5904, 734, 914, 1514, 9554, 369, 1503, 907, 790, 8537, 918, 1280, 2673, 3359, 471, 2540, 4684, 96, 342, 27111, 490]]]]
n_pt [19707824, [0, 4], [[[0], [1087, 339, 489, 263, 1786, 824, 82, 334, 317, 805, 96, 327, 

n_pt [19950146, [0, 7], [[[0], [16077, 117, 109, 333, 128, 6165, 27306, 823, 1409, 800, 1175, 114, 84, 81, 86, 10612, 4944, 3122, 6159, 6160, 12744]], [[66], [86, 7860, 925, 6165, 84, 79, 333, 81]], [[201], [84, 8907, 6162, 6481, 2795, 18859, 367, 1398, 1020, 342, 86, 81, 4806, 333, 360, 919, 479]], [[19], [7471, 27307, 27308, 16933, 7468, 1904, 7925, 86, 734, 2795, 1409, 100, 1031, 4761, 1198, 3349, 4944, 1127, 333, 27309, 477, 84, 2354, 122, 4810, 2304, 1020, 27306, 2703, 1157, 8892, 4561, 10612, 1142, 4917, 1911, 114, 259, 1136, 81]]]]
n_pt [19950615, [0, 4], [[[0], [7258, 1653, 1553, 636, 855, 1359, 1358, 7086, 716, 148, 2306, 3191, 1769]]]]
n_pt [19950645, [0, 2], [[[0], [1619, 3173, 603, 41, 958, 2082, 502, 1, 26, 1036, 20, 39, 2080, 221, 156, 210, 160, 148, 211]], [[1986], [4291, 658, 750, 625, 184, 11, 1619, 381, 39, 2082, 30, 156, 603, 41, 3448, 26, 502, 1, 221, 148]], [[67], [2035, 190, 603, 148, 1, 161, 191, 187, 230, 232, 1736, 1015, 231, 626, 595, 30, 536, 1619, 502, 39, 2

In [ ]:
### Extract code descriptions as we will use later

diag_desc = pd.read_csv(mimic4_path+'/hosp/d_icd_diagnoses.csv.gz', compression='gzip', header=0)
diag_desc['event_code']='D_ICD'+diag_desc['icd_version'].astype('str')+'_'+diag_desc['icd_code']
proc_desc= pd.read_csv(mimic4_path+'/hosp/d_icd_procedures.csv.gz', compression='gzip', header=0)
proc_desc['event_code']='P_ICD'+proc_desc['icd_version'].astype('str')+'_'+proc_desc['icd_code']
diag_desc['cat']='Diag'
proc_desc['cat']='Proc'
code_desc=pd.concat([diag_desc[['event_code','cat','long_title']],proc_desc[['event_code','cat','long_title']]])
code_desc.to_csv(output_proc+'/code_desc.tsv',sep='\t',index=False)

## Data in OMOP format (MIMIC IV Demo Data)

> First we need to define our objective: 
  This is a demo data of 100 patients, so we will use all patients till last admission to predict mortality (so note the difference from the previous cohort, is that we don't retrict to icu stays and it is not just in-hospital mortality , i.e we wase our conditions for the sake of the Demo)

Again we will prepare to predict both binary and survival

So we need a label file that include: 'subject_id' , 'mortality_indicator' , 'time from index date to death'

and then extract all patient diagnosis and procedures available till the index date and use the linked visit admission or discharge date to later define the sequence of visits

  So our steps:

  1. Identify the patients label (died or not) --> Death Table
  2. Find out the index date per patient (admission date for last encounter/visit) ----> visit_occurence
  3. Extract diagnosis and procedures, along with the linked visit admission or discharge date





In [ ]:
#!wget -r -N -c -np https://physionet.org/files/mimic-iv-demo-omop/0.9/ -P /content/drive/MyDrive/pytorch_ehr/Pytorch_EHR_Tutorial/Data_Prep/data 

In [14]:
mimic4_omop_pth='/content/drive/MyDrive/pytorch_ehr/Pytorch_EHR_Tutorial/Data_Prep/data/physionet.org/files/mimic-iv-demo-omop/0.9/1_omop_data_csv/'
mo_db_pth='/content/drive/MyDrive/pytorch_ehr/Pytorch_EHR_Tutorial/Data_Prep/data/physionet.org/files/'


### Let's understand the data First



In [15]:
pt_died = pd.read_csv(mimic4_omop_pth+'death.csv', header=0)
pt_died =pt_died[['person_id','death_date']]

In [16]:
pts = pd.read_csv(mimic4_omop_pth+'person.csv', header=0)
pts 


person_id  ...  ethnicity_source_concept_id
0   3589912774911670296  ...                   2000001408
1  -3210373572193940939  ...                   2000001408
2   -775517641933593374  ...                            0
3  -2575767131279873665  ...                            0
4  -8970844422700220177  ...                            0
..                  ...  ...                          ...
95 -7671795861352464589  ...                            0
96  5734523979606454056  ...                            0
97  1532249960797525190  ...                            0
98  5894416985828315484  ...                            0
99 -3780452582396805474  ...                            0

[100 rows x 18 columns]

In [17]:
vts = pd.read_csv(mimic4_omop_pth+'visit_occurrence.csv', header=0)
vts[['person_id','visit_occurrence_id','visit_start_datetime','visit_end_datetime','admitting_source_value','discharge_to_source_value','preceding_visit_occurrence_id']]

person_id  ...  preceding_visit_occurrence_id
0    4783904755296699562  ...                  -3.100296e+18
1   -6225647829918357531  ...                  -2.238366e+18
2    7918537411740862407  ...                  -8.600570e+18
3   -6225647829918357531  ...                   4.782862e+18
4    7155255168997124770  ...                  -3.275690e+18
..                   ...  ...                            ...
847  4498126063475867818  ...                            NaN
848  4498126063475867818  ...                            NaN
849  6128703162302148003  ...                            NaN
850 -3908355835367628651  ...                            NaN
851  3192038106523208432  ...                            NaN

[852 rows x 7 columns]

In [18]:
diag = pd.read_csv(mimic4_omop_pth+'condition_occurrence.csv', header=0)
diag

condition_occurrence_id  ...  condition_status_concept_id
0          7000818053728441484  ...                          NaN
1         -3514320024333679102  ...                          NaN
2         -6297447354934110463  ...                          NaN
3          3131132784874295309  ...                          NaN
4          2246709778332812674  ...                          NaN
...                        ...  ...                          ...
16436      5160751222712405682  ...                          NaN
16437      7817722518091634880  ...                          NaN
16438      5631597446422224513  ...                          NaN
16439      8817407860694965134  ...                          NaN
16440     -3089187292354338535  ...                          NaN

[16441 rows x 16 columns]

#### Some data quality check

In [19]:
diag['condition_source_value']=diag['condition_source_value'].str.strip()
v_diag=diag[diag['condition_source_value'].str.strip().str.lower().str.startswith('v')][['condition_source_value','condition_type_concept_id']].drop_duplicates() #32821 are normal diagnosis, 32817 are those derived from ECG/notes
e_diag=diag[diag['condition_source_value'].str.strip().str.lower().str.startswith(('e0','e8','e9'))][['condition_source_value','condition_type_concept_id']].drop_duplicates() #32821 are normal diagnosis, 32817 are those derived from ECG/notes


In [20]:
diag_desc = pd.read_csv(mimic4_path+'/hosp/d_icd_diagnoses.csv.gz', compression='gzip', header=0)
v_diag=v_diag.merge(diag_desc, how='left' ,left_on='condition_source_value',right_on='icd_code')
v_diag[v_diag['icd_code'].duplicated(keep=False)]

condition_source_value  ...                                         long_title
3                    V462  ...  Other dependence on machines, supplemental oxygen
4                    V462  ...  Person on outside of car injured in collision ...
7                    V641  ...  Surgical or other procedure not carried out be...
8                    V641  ...  Passenger in heavy transport vehicle injured i...
9                    V643  ...        Procedure not carried out for other reasons
10                   V643  ...  Unspecified occupant of heavy transport vehicl...
14                   V860  ...            Estrogen receptor positive status [ER+]
15                   V860  ...  Driver of special all-terrain or other off-roa...
17                   V090  ...  Infection with microorganisms resistant to pen...
18                   V090  ...  Pedestrian injured in nontraffic accident invo...

[10 rows x 5 columns]

In [21]:
e_diag=e_diag.merge(diag_desc, how='left' ,left_on='condition_source_value',right_on='icd_code')
e_diag[e_diag['icd_code'].duplicated(keep=False)]

condition_source_value  ...                                         long_title
12                  E8809  ...   Accidental fall on or from other stairs or steps
13                  E8809  ...  Other disorders of plasma-protein metabolism, ...
23                  E8339  ...  Fall on stairs or ladders in water transport i...
24                  E8339  ...           Other disorders of phosphorus metabolism
29                  E8881  ...    Fall resulting in striking against other object
30                  E8881  ...                                 Metabolic syndrome

[6 rows x 5 columns]

In [22]:
pts_toexclude=diag[diag['condition_source_value'].isin(['E8809','E8339','E8881','V090','V860','V462','V641','V643'])]['person_id'].unique().tolist()
len(pts_toexclude)

11

In [23]:
pt_died[pt_died['person_id'].isin(pts_toexclude)] ### I will exclude 4 out of originally 14 cases :), It is a decision point, exclude the whole pt or just those diag records, I prefer to exclude the full patient if it is a small % but for the sake of the demo, I'll only drop those diag and similarly procedures

person_id  death_date
2   1194579079287927665  2177-03-29
8  -3908355835367628651  2137-09-02
9   4783904755296699562  2116-03-12
13 -9066461348710750663  2185-01-22

In [24]:
proc_o = pd.read_csv(mimic4_omop_pth+'procedure_occurrence.csv', header=0)
proc_o[['person_id','procedure_source_value','procedure_datetime','visit_occurrence_id']]

person_id  ...  visit_occurrence_id
0      4783904755296699562  ...  -433474223361412760
1      7918537411740862407  ...  7730200099818586525
2      4498126063475867818  ...  2514722389640694708
3      8090044958540695372  ...  6734319289435533605
4      5863607150722936210  ... -5935156580867756808
...                    ...  ...                  ...
18442 -3908355835367628651  ... -3115724380369486208
18443 -3908355835367628651  ... -3115724380369486208
18444 -6225647829918357531  ... -6661057387050813606
18445 -6225647829918357531  ... -8296465610050985060
18446  4352191084057402257  ... -6997065935457482721

[18447 rows x 4 columns]

In [25]:
proc_desc = pd.read_csv(mimic4_path+'/hosp/d_icd_procedures.csv.gz', compression='gzip', header=0)
#proc_desc['icd_code']=proc_desc['icd_code'].str.strip()
proc_codes=proc_o[['procedure_source_value','procedure_type_concept_id']].drop_duplicates() #32821 are normal diagnosis, 32817 are those derived from ECG/notes
proc_codes['procedure_source_value']=proc_codes['procedure_source_value'].str.strip()
proc_codes=proc_codes.merge(proc_desc, how='left' ,left_on='procedure_source_value',right_on='icd_code')
proc_codes

procedure_source_value  ...                                         long_title
0                    19301  ...                                                NaN
1                    19303  ...                                                NaN
2                    27235  ...                                                NaN
3                    36252  ...                                                NaN
4                    36830  ...                                                NaN
..                     ...  ...                                                ...
306                B54BZZA  ...  Ultrasonography of Right Lower Extremity Veins...
307                BT1DYZZ  ...  Fluoroscopy of Right Kidney, Ureter and Bladde...
308                BT1FYZZ  ...  Fluoroscopy of Left Kidney, Ureter and Bladder...
309                D7021ZZ  ...  Beam Radiation of Spleen using Photons 1 - 10 MeV
310                DW021ZZ  ...   Beam Radiation of Chest using Photons 1 - 10 MeV

[311 rows x 5 columns]

In [26]:
proc_codes.describe(include='all')

procedure_source_value  ...                                         long_title
count                     311  ...                                                159
unique                    311  ...                                                159
top                     43237  ...  Introduction of Other Therapeutic Substance in...
freq                        1  ...                                                  1
mean                      NaN  ...                                                NaN
std                       NaN  ...                                                NaN
min                       NaN  ...                                                NaN
25%                       NaN  ...                                                NaN
50%                       NaN  ...                                                NaN
75%                       NaN  ...                                                NaN
max                       NaN  ...                                                NaN

[11 rows x 5 columns]

In [27]:
proc_desc[proc_desc['icd_code'].str.contains('36830')]

Empty DataFrame
Columns: [icd_code, icd_version, long_title]
Index: []

In [28]:
proc[proc['icd_code'].str.contains('683')]['icd_code'].drop_duplicates()

40        6839
856       8683
7481      6831
141081    5683
Name: icd_code, dtype: object

**something is wrong mainly because those code are CPT not ICD procedures** :) 

you can just google "procedure icd 36830" ---> again this is a decision point and for the sake of the demo, I will just ignore those, in real practice, I make sure I include them 


And here, where terminology normalization will be helpful ---- https://github.com/ZhiGroup/terminology_representation




In [29]:
proc_codes=proc_codes.dropna()
proc_codes[proc_codes['icd_code'].duplicated(keep=False)] #### so no duplicates issue

Empty DataFrame
Columns: [procedure_source_value, procedure_type_concept_id, icd_code, icd_version, long_title]
Index: []

##### Alternate way to prepocess the data using sql for example you can use the below code to create a sqlite database, and you can move to sql from there

In [30]:
import sqlite3
conn = sqlite3.connect(mo_db_pth+'mimic_omop.db')
pts[['person_id','year_of_birth','gender_source_value','race_source_value','ethnicity_source_value']].to_sql('pts_omop', conn , if_exists='replace', index=False)
vts[['person_id','visit_occurrence_id','visit_start_datetime','visit_end_datetime','admitting_source_value','discharge_to_source_value','preceding_visit_occurrence_id']].to_sql('visits_omop', conn , if_exists='replace', index=False)
pd.read_csv(mimic4_omop_pth+'death.csv', header=0).to_sql('death_omop', conn , if_exists='replace', index=False)
diag[['person_id','visit_occurrence_id','condition_source_value','condition_start_datetime','condition_end_datetime']].to_sql('diag_omop', conn , if_exists='replace', index=False)
proc_o[['person_id','visit_occurrence_id','procedure_source_value','procedure_datetime']].to_sql('proc_omop', conn , if_exists='replace', index=False)
diag_desc.to_sql('diag_desc', conn, if_exists='replace', index=False)
proc_desc.to_sql('diag_desc', conn, if_exists='replace', index=False)
conn.close()
